In [2]:
import numpy as np
import time

class gaussSolve:
    '''Class for solving linear equation with gaussian elimination'''
        
    def __init__(self,A0,b0,pivotTF=True,calcInv=True):
        self.A0=A0
        self.b0=b0
        self.N=len(b0)
        self.pivotTF=pivotTF
    
        Aandb=self.forward_elim(A0,b0)
        self.Aech=Aandb[0]
        self.bEch=Aandb[1]
        self.nPivots=Aandb[2]
        self.nSteps=Aandb[3]
        
        self.x=self.back_substitute(self.Aech,self.bEch)

        self.det=self.determinant(self.Aech,isEchelon=True,nPivots=self.nPivots)
        
        self.inv=self.inverse(A0) if calcInv else []   
       
        
    def __str__(self):
        
        return 'A original:\n'+str(self.A0)+'\n b orignial: '+str(self.b0) \
                +'\n A echelon: \n'+str(self.Aech)+'\n b echelon: '+str(self.bEch) \
                + '\n \n Determinant: ' + str(self.det) +'\n Inverse: \n'+str(self.inv) \
                +'\n \n x: '+str(self.x)
   
    def forward_elim(self,A0,b0):
        '''Perform forward elimination steps'''
        
        A=np.copy(A0)
        b=np.copy(b0)
        
        # TEST: lets see how many steps
        nSteps=0
        
        nPivots=0
        for column in range(self.N):
        
            if self.pivotTF:
                A,pivoted=self.pivot(A,b,column)
                if pivoted: nPivots+=1
            
            for row in range(column+1,self.N):              
                try:
                    multFac=(A[row,column]/A[column,column])
                except:
                    print("Issue with forward elimination!")
                A[row,:]-=multFac*A[column,:]
                b[row]-=multFac*b[column]
                
                nSteps+=1

        return A,b,nPivots,nSteps
            
    def back_substitute(self,A,b):
        '''Perform back substitution on row echelon matrix'''
        
        x=np.zeros(self.N)
        x[-1]=b[-1]/A[self.N-1,self.N-1]
        
        for row in range(self.N-2,-1,-1):
            for column in range(self.N-1,row,-1):
                x[row]-=x[column]*A[row,column]/A[row,row]
            x[row]+=b[row]/A[row,row]
            
        return x
            
    def pivot(self,A,b,column):
        '''Puts row with largest scaled value in column at row'''
        
        # Make sure we are only looking below row=column
        pivotRow=np.argmax((A[:,column]/np.max(np.abs(A), 1))[column:self.N])+column # Figure out if leading column has largest value
        A[[column,pivotRow]]=A[[pivotRow,column]] # If not, these lines will pivot
        b[[column,pivotRow]]=b[[pivotRow,column]]
        
        pivoted=True if column != pivotRow else False
        
        return A,pivoted

    def determinant(self,A,isEchelon=False,nPivots=-1):
        '''Calculate the determinant Gauss elimination'''
        
        if isEchelon: 
            if nPivots >= 0:
                return (-1.0)**nPivots*np.prod(np.diagonal(A))
            else:
                print('Must supply nPivots for determinant of Echelon matrix')
                raise
        
        bDummy=np.zeros(self.N)
        
        Aech,bDummy,nPivots=self.forward_elim(A,bDummy)
        
        return (-1.0)**nPivots*np.prod(np.diagonal(Aech))
    
    def inverse(self,A0):
        '''Calculate the inverse via Gauss elimination'''
        
        invA=np.identity(self.N)
        
        for column in range(self.N):
            A,e,nPivots,nSteps=self.forward_elim(A0,invA[:,column])
            x=self.back_substitute(A,e)
            
            invA[:,column]=x
        
        return invA
            

In [7]:
# Some examples:

A=np.array([[1,1,1],[-1,2,0],[2,0,1]],float)
b=np.array([6.0,3.0,5.0])

#eps=1e-15
#A=np.array([[eps,1,1],[1,1,0],[1,0,1]],float)
#b=np.array([5.0,3.0,4.0])

gaussTest=gaussSolve(A,b)
#gaussTest=gaussSolve(A,b,pivotTF=False)

print(gaussTest,'\n')
print('numpy determinant: ',np.linalg.det(A),'\n')
print('numpy inverse: \n',np.linalg.inv(A),'\n')
print('numpy solve x: ',np.linalg.solve(A,b),'\n')


A original:
[[ 1.  1.  1.]
 [-1.  2.  0.]
 [ 2.  0.  1.]]
 b orignial: [6. 3. 5.]
 A echelon: 
[[ 1.          1.          1.        ]
 [ 0.          3.          1.        ]
 [ 0.          0.         -0.33333333]]
 b echelon: [ 6.  9. -1.]
 
 Determinant: -1.0
 Inverse: 
[[-2.  1.  2.]
 [-1.  1.  1.]
 [ 4. -2. -3.]]
 
 x: [1. 2. 3.] 

numpy determinant:  -1.0 

numpy inverse: 
 [[-2.  1.  2.]
 [-1.  1.  1.]
 [ 4. -2. -3.]] 

numpy solve x:  [1. 2. 3.] 



In [8]:
# Let's try a BIG random matrix
nMatrix=10
A=np.random.rand(nMatrix,nMatrix)
b=np.random.rand(nMatrix)

gaussTest=gaussSolve(A,b)

print(gaussTest.x,'\n')
print('numpy solve x: ',np.linalg.solve(A,b),'\n')
print(gaussTest.inv)

[-0.52130256 -5.4173069   1.37716833 -0.68982284  0.81873291  0.89288622
  0.25106709 -0.33966627  4.49275801 -0.44882533] 

numpy solve x:  [-0.52130256 -5.4173069   1.37716833 -0.68982284  0.81873291  0.89288622
  0.25106709 -0.33966627  4.49275801 -0.44882533] 

[[ 7.97511472e-01 -4.36594570e-01 -1.78234954e+00 -1.81456670e+00
  -4.40843085e-01  7.62320385e-01  3.25709416e-01 -1.60947272e-01
   5.34525052e-03  1.72776885e+00]
 [-1.50884671e+00 -1.89509175e+00  6.65210957e+00  5.23766756e+00
  -1.75484704e+00  3.11058290e+00 -6.82534231e+00  3.79849620e+00
  -5.42968811e-01 -2.75991605e+00]
 [-7.72459407e-01  1.95218417e+00  1.31835491e+00  4.76615124e-01
   4.82514718e-01 -1.28584486e+00 -9.66538926e-02 -2.61574327e-01
   1.67378118e+00 -2.84418188e+00]
 [-2.85535815e-01 -1.22756502e+00  1.87503181e+00  1.55167630e+00
   1.44872404e-01  7.36161369e-01 -1.81975742e+00  2.69732198e-01
   5.38893710e-01 -5.12147901e-01]
 [ 1.15848257e+00 -2.04663806e+00 -1.72016135e+00 -2.50764921e+00


In [20]:
# Example of a singular matrix:

A = np.array([ [ 1, 2, 3], 
               [ 4, 5, 6], 
               [ 7, 8, 9] ], dtype=np.float64)
b = np.array([5, -1, 2], dtype=np.float64)

gaussSing=gaussSolve(A,b)

print(gaussSing)

print('Condition number: ',np.linalg.cond(A)*np.finfo(float).eps)

A original:
[[1. 2. 3.]
 [4. 5. 6.]
 [7. 8. 9.]]
 b orignial: [ 5. -1.  2.]
 A echelon: 
[[7.         8.         9.        ]
 [0.         0.42857143 0.85714286]
 [0.         0.         0.        ]]
 b echelon: [ 2.         -2.14285714  9.        ]
 
 Determinant: -0.0
 Inverse: 
[[ nan  nan  nan]
 [-inf  inf -inf]
 [ inf -inf  inf]]
 
 x: [ nan -inf  inf]
Condition number:  11.2183139323341


/var/folders/r3/x1_dzkd17bl79jcx6v49vh600000gr/T/ipykernel_98491/328951155.py:78: RuntimeWarning: invalid value encountered in divide
  pivotRow=np.argmax((A[:,column]/np.max(np.abs(A), 1))[column:self.N])+column # Figure out if leading column has largest value
/var/folders/r3/x1_dzkd17bl79jcx6v49vh600000gr/T/ipykernel_98491/328951155.py:65: RuntimeWarning: divide by zero encountered in scalar divide
  x[-1]=b[-1]/A[self.N-1,self.N-1]
/var/folders/r3/x1_dzkd17bl79jcx6v49vh600000gr/T/ipykernel_98491/328951155.py:69: RuntimeWarning: invalid value encountered in scalar subtract
  x[row]-=x[column]*A[row,column]/A[row,row]


In [21]:
# Banded matricies

class gaussSolveBanded(gaussSolve):
    
    def __init__(self,A0,b0,nBands,pivotTF=True,calcInv=False):
        
        self.nBands=nBands
        gaussSolve.__init__(self,A0,b0,pivotTF=True,calcInv=False)

    def forward_elim(self,A0,b0):
        '''Perform forward elimination steps for banded matrix'''
        
        A=np.copy(A0)
        b=np.copy(b0)
        
        # TEST: lets see how many steps
        nSteps=0
        
        nPivots=0 # No pivots, or we lose the banded nature
        for column in range(self.N):
            for band in range(column+1,min(self.N,column+1+self.nBands)):
                try:
                    multFac=(A[band,column]/A[column,column])
                except:
                    print(band,column)
                    print("Issue with forward elimination!")
                    
                A[band,:]-=multFac*A[column,:]
                b[band]-=multFac*b[column]

                nSteps+=1
                
        return A,b,nPivots,nSteps
    


In [25]:
# Construct random banded matrix
nBands=3
nMatrix=100
A=np.random.rand(nMatrix,nMatrix)
b=np.random.rand(nMatrix)

for ii in range(nMatrix):
    for jj in range(nMatrix):
        if abs(ii-jj)>nBands: A[ii,jj]=0.0
            
np.set_printoptions(linewidth=100)

# Time the normal algorithm versus the banded one
start = time.perf_counter()
gaussBand=gaussSolve(A,b,calcInv=False)
end = time.perf_counter()
print("Time for gaussSolve:", end - start)
print(gaussBand.x)

print()

start = time.perf_counter()
gaussBand2=gaussSolveBanded(A,b,nBands,calcInv=False)
end = time.perf_counter()
print("Time for gaussSolveBanded:", end - start)
print(gaussBand2.x)


Time for gaussSolve: 0.018264791986439377
[ 4.73296122e-01 -3.00950942e-01 -1.24516903e+00  3.39492485e+00 -1.68133513e+00 -3.40371583e-01
 -1.71368601e+00  1.50863326e+00  1.64099284e+00 -1.73548382e+00  1.62759888e+00  7.89291280e-01
  1.35235411e+00 -3.47992076e+00  2.63791943e+00 -9.26827937e-01 -2.29354458e+00  3.07037750e+00
 -2.91431820e+00  1.88147711e+00 -9.33977222e+00  4.78509745e+00  1.23307770e+01 -7.14445106e+00
 -2.38590937e+00 -3.82396248e+00 -2.16251622e+00 -3.69837434e+00  6.98180923e+00  6.69064478e+00
  4.88928185e+00 -8.42489898e+00 -5.22318987e+00 -3.09819271e+00 -6.13137781e+00  8.57951377e+00
 -2.62071731e+00  9.22030606e+00  4.80284415e+00 -8.21517575e+00 -8.50884028e+00  1.74673909e+00
  9.24950461e+00  6.18916546e+00 -1.26046521e-01  1.14606874e+01 -1.11781980e+01 -1.23630360e+01
 -2.59208239e+00  1.11193452e+01 -1.33423173e+01  2.11241496e+01  2.76915011e+00 -9.92494097e+00
  4.80888399e+00 -1.01672197e+01 -4.73351748e+00  1.13710817e+01 -1.35062917e+01  2.3